### 5.3.3 스타벅스 매장 수와 인구수 비교

In [1]:
# 예제 5-65 라이브러리 임포트
import pandas as pd
import json
import folium

In [2]:
# 예제 5-66 서울시 시군구별 통계 데이터 불러오기
seoul_sgg_stat = pd.read_excel('./files/4_5_seoul_sgg_stat.xlsx')
seoul_sgg_stat.head()

시군구코드  시군구명         위도          경도  스타벅스_매장수  주민등록인구    종사자수   사업체수
0  11320   도봉구  37.665861  127.031767         2  345041   68669  18455
1  11380   은평구  37.617612  126.922700         8  490253   87693  24179
2  11230  동대문구  37.583801  127.050700         8  364962  143858  32994
3  11590   동작구  37.496504  126.944307         9  406715  103915  19609
4  11545   금천구  37.460097  126.900155        10  253344  223058  30080

In [3]:
# 예제 5-67 서울시 시군구 행정 경계 지도 파일 불러오기
sgg_geojson_file_path = './maps/seoul_sgg.geojson'
seoul_sgg_geo_2 = json.load(open(sgg_geojson_file_path, encoding='utf-8'))

In [4]:
# 예제 5-68  서울시 시군구별 주민등록인구수 단계구분도 지도 시각화
starbucks_choropleth = folium.Map(
    location=[37.573050, 126.979189],
    tiles='CartoDB dark_matter',
    zoom_start=11
)

folium.Choropleth(
    geo_data=seoul_sgg_geo_2,
    data=seoul_sgg_stat,
    columns=['시군구명', '주민등록인구'],
    fill_color = 'YlGn',
    fill_opacity=0.7,
    line_opacity=0.5,
    key_on='properties.SIG_KOR_NM'
    ).add_to(starbucks_choropleth)

starbucks_choropleth

In [5]:
# 예제 5-69  인구 만 명당 스타벅스 매장 수 칼럼 추가
seoul_sgg_stat['만명당_매장수'] = seoul_sgg_stat['스타벅스_매장수']/(seoul_sgg_stat['주민등록인구']/10000)

In [6]:
# 예제 5-70  인구 만 명당 스타벅스 매장 수 지도 시각화
SGG_GEOJSON_FILE_PATH = './maps/seoul_sgg.geojson'
seoul_sgg_geo_1 = json.load(open(SGG_GEOJSON_FILE_PATH, encoding='utf-8'))

viz_map_1 = folium.Map(
    location=[37.573050, 126.979189],
    tiles='CartoDB dark_matter',
    zoom_start=11
)

# 지도 스타일 지정 함수
def style_function(feature):
    return {
        'opacity': 0.7,
        'weight': 1,
        'fillOpacity':0,
    }

folium.GeoJson(
    seoul_sgg_geo_2,
    style_function=style_function,
).add_to(viz_map_1)
# 만명당 매장수 기준 상위 10% 추출 값
top = seoul_sgg_stat ['만명당_매장수'].quantile(0.9)
for idx in seoul_sgg_stat.index:
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    r = seoul_sgg_stat.loc[idx, '만명당_매장수']
    if r > top:
        fillColor = '#FF3300' # (Red)
    else:
        fillColor = '#CCFF33' # (Green)
    
    folium.CircleMarker(
        location=[lat, lng], 
        color='#FFFF00',     # (Yellow)
        fill_color=fillColor, 
        fill_opacity=0.7,
        weight=1.5,
        radius= r * 10
    ).add_to(viz_map_1)

viz_map_1

### 5.3.4 스타벅스 매장 수와 사업체 수 비교

In [7]:
# 예제 5-71 신규 칼럼을 생성해 값 입력
seoul_sgg_stat['종사자수_만명당_매장수'] = seoul_sgg_stat['스타벅스_매장수']/(seoul_sgg_stat['종사자수']/10000)
seoul_sgg_stat.head()

시군구코드  시군구명         위도          경도  스타벅스_매장수  주민등록인구    종사자수   사업체수  \
0  11320   도봉구  37.665861  127.031767         2  345041   68669  18455   
1  11380   은평구  37.617612  126.922700         8  490253   87693  24179   
2  11230  동대문구  37.583801  127.050700         8  364962  143858  32994   
3  11590   동작구  37.496504  126.944307         9  406715  103915  19609   
4  11545   금천구  37.460097  126.900155        10  253344  223058  30080   

    만명당_매장수  종사자수_만명당_매장수  
0  0.057964      0.291252  
1  0.163181      0.912273  
2  0.219201      0.556104  
3  0.221285      0.866092  
4  0.394720      0.448314

In [8]:
# 예제 5-72 종사자 수 1만 명당 스타벅스 매장 수 시각화
seoul_sgg_geo_1 = json.load(open(SGG_GEOJSON_FILE_PATH, encoding='utf-8'))

viz_map_1 = folium.Map(
    location=[37.573050, 126.979189],
    tiles='CartoDB dark_matter',
    zoom_start=11
)

folium.GeoJson(
    seoul_sgg_geo_1,
    style_function=style_function,
).add_to(viz_map_1)

top = seoul_sgg_stat['종사자수_만명당_매장수'].quantile(0.9)
for idx in seoul_sgg_stat.index:
    name = seoul_sgg_stat.at[idx, '시군구명']
    lat = seoul_sgg_stat.loc[idx, '위도']
    lng = seoul_sgg_stat.loc[idx, '경도']
    r = seoul_sgg_stat.loc[idx, '종사자수_만명당_매장수']
    
    if r > top:
        fillColor = '#FF3300'
    else:
        fillColor = '#CCFF33'
    
    folium.CircleMarker(
        location=[lat, lng], 
        color='#FFFF00', 
        fill_color=fillColor, 
        fill_opacity=0.7,
        weight=1.5,
        radius= r * 10
    ).add_to(viz_map_1)

viz_map_1